### Call back

In [1]:
import os
from glob import glob
from datetime import datetime

import numpy as np
import tensorflow as tf
from tensorflow.keras import layers
from tensorflow.keras import datasets

import matplotlib.pyplot as plt
%matplotlib inline
%load_ext tensorboard

In [43]:
tf.__version__

'2.3.0'

### hyerparameter tunning

In [2]:
num_epochs = 10
batch_size = 32
learning_rate = 0.001
dropout_rate = 0.5
input_shape = (32,32,3)
num_classes = 10

### Build Model

In [3]:
inputs  = layers.Input(input_shape)

net = layers.Conv2D(32, (3,3), padding = 'SAME')(inputs)
net = layers.Activation('relu')(net)
net = layers.Conv2D(32, (3,3), padding = 'SAME')(net)
net = layers.Activation('relu')(net)
net = layers.Dropout(dropout_rate)(net)

net = layers.Conv2D(64, (3,3), padding = 'SAME')(net)
net = layers.Activation('relu')(net)
net = layers.Conv2D(64, (3,3), padding = 'SAME')(net)
net = layers.Activation('relu')(net)
net = layers.Dropout(dropout_rate)(net)

net = layers.Flatten()(net)
net = layers.Dense(512)(net)
net = layers.Activation('relu')(net)
net = layers.Dropout(dropout_rate)(net)
net = layers.Dense(num_classes)(net)
net = layers.Activation('softmax')(net)

model = tf.keras.Model(inputs = inputs, outputs = net, name = 'Basic_CNN')


In [4]:
model.compile(optimizer = tf.keras.optimizers.Adam(learning_rate),
              loss = 'sparse_categorical_crossentropy', # onehot이 아닌 label 번호를 받을 예정이다
              metrics = ['accuracy'])

### data preprocess

In [5]:
os.listdir('cifar')

['labels.txt', 'test', 'train']

In [6]:
train_paths = glob('cifar/train/*.png')[:1000]
test_paths = glob('cifar/test/*.png')[:1000]

len(train_paths), len(test_paths)

(1000, 1000)

In [7]:
path = train_paths[0]
path.split('_')

['cifar/train\\0', 'frog.png']

In [8]:
def get_class_name(path):
    return path.split('_')[-1].replace('.png', '')

In [9]:
train_labels = [get_class_name(path) for path in train_paths]
class_names = np.unique(train_labels)

In [10]:
class_names

array(['airplane', 'automobile', 'bird', 'cat', 'deer', 'dog', 'frog',
       'horse', 'ship', 'truck'], dtype='<U10')

In [11]:
def get_label(path):
    fname = tf.strings.split(path, '_')[-1]
    lbl_name = tf.strings.regex_replace(fname, '.png', '')
    onehot = tf.cast(lbl_name == class_names, tf.uint8)
    return tf.argmax(onehot) #이번만 onehot이 아니라 label번호로

In [12]:
def load_image_label(path):
    gfile = tf.io.read_file(path)
    image = tf.io.decode_image(gfile)
    image = tf.cast(image, tf.float32) / 255. # rescale
    label = get_label(path)
    return image, label

In [13]:
def image_preprocess(image, label):
    image = tf.image.random_flip_up_down(image)
    image = tf.image.random_flip_left_right(image)
    return image, label

In [14]:
AUTOTUNE = tf.data.experimental.AUTOTUNE

In [15]:
train_dataset = tf.data.Dataset.from_tensor_slices(train_paths)
train_dataset = train_dataset.map(load_image_label, num_parallel_calls = AUTOTUNE)
train_dataset = train_dataset.map(image_preprocess, num_parallel_calls = AUTOTUNE)
train_dataset = train_dataset.batch(batch_size)
train_dataset = train_dataset.repeat()

In [16]:
test_dataset = tf.data.Dataset.from_tensor_slices(test_paths)
test_dataset = test_dataset.map(load_image_label, num_parallel_calls = AUTOTUNE)

test_dataset = test_dataset.batch(batch_size)
test_dataset = test_dataset.repeat()

### callbacks

In [17]:
logdir = os.path.join('logs', datetime.now().strftime('%Y%m%d - %H%M%S'))

In [18]:
tensorboard=tf.keras.callbacks.TensorBoard(
    log_dir = logdir,
    write_graph = True,
    write_images = True,
    histogram_freq = 1
)

In [19]:
# %tensorboard --logdir logs 8008

### training

In [20]:
steps_per_epoch = len(train_paths) // batch_size
validation_steps = len(test_paths)// batch_size

model.fit_generator(
    train_dataset,
    steps_per_epoch = steps_per_epoch,
    validation_data = test_dataset,
    validation_steps = validation_steps,
    epochs = num_epochs,
    callbacks = [tensorboard]
)

Instructions for updating:
Please use Model.fit, which supports generators.
Epoch 1/10
 1/31 [..............................] - ETA: 0s - loss: 2.3336 - accuracy: 0.0625WARNING:tensorflow:From C:\Users\hapet\anaconda3\envs\tensorflow\lib\site-packages\tensorflow\python\ops\summary_ops_v2.py:1277: stop (from tensorflow.python.eager.profiler) is deprecated and will be removed after 2020-07-01.
Instructions for updating:
use `tf.profiler.experimental.stop` instead.
31/31 [==============================] - 17s 562ms/step - loss: 2.4863 - accuracy: 0.1079 - val_loss: 2.2705 - val_accuracy: 0.1169
Epoch 2/10
31/31 [==============================] - 17s 556ms/step - loss: 2.2773 - accuracy: 0.1260 - val_loss: 2.2504 - val_accuracy: 0.0968
Epoch 3/10
31/31 [==============================] - 18s 586ms/step - loss: 2.2255 - accuracy: 0.1694 - val_loss: 2.1565 - val_accuracy: 0.1663
Epoch 4/10
31/31 [==============================] - 17s 558ms/step - loss: 2.1877 - accuracy: 0.1860 - val_loss: 2.

### lambda callback

In [51]:
import sklearn.metrics
import itertools
import io

file_writer_cm = tf.summary.create_file_writer(logdir + 'cm')

def plot_to_image(figure):
    
    buf = io.BytesIO()
    plt.savefig(buf, format = 'png')
    plt.close(figure)
    buf.seek(0)
    image = tf.image.decode_png(buf.getvalue(), channels = 4)
    image = tf.expand_dims(image,0)
    return image
def plot_confusion_matrix(cm, class_names):
    figure = plt.figure(figsize = (8,8))
    plt.imshow(cm, interpolation = 'nearest', cmap = plt.cm.Blues)
    plt.title('Confusion matrix')
    plt.colorbar()
    tick_marks = np.arange(len(class_names))
    plt.xticks(tick_marks,class_names, rotation = 45)
    plt.yticks(tick_marks, class_names)
    
    cm =np.around(cm.astype('float') / cm.sum(axis = 1)[:, np.newaxis], decimals = 2)
    
    threshold = cm.max()/2
    for i, j, in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        color = 'white' if cm[i,j] > threshold else "black"
        plt.text(j,i,cm[i,j], horizontalalignment = 'center', color= color)
    plt.tight_layout()
    plt.ylabel('True label')
    plt.xlabel('Predicted label')
    return figure

In [52]:
test_images, test_labes = next(iter(test_dataset))

def log_confusion_matrix(epoch, logs):
    test_pred_raw = model.predict(test_images)
    test_pred = np.argmax(test_pred_raw, axis = 1)
    
    cm = sklearn.metrics.confusion_matrix(test_labes, test_pred)
    figure = plot_confusion_matrix(cm, class_names = class_names)
    cm_image = plot_to_image(figure)
    
    with file_writer_cm.as_default():
        tf.summary.image("Confusion Matrix", cm_image, step = epoch)

In [53]:
cm_callback = tf.keras.callbacks.LambdaCallback(on_epoch_end = log_confusion_matrix)

In [54]:
steps_per_epoch = len(train_paths) // batch_size
validation_steps = len(test_paths)// batch_size

model.fit_generator(
    train_dataset,
    steps_per_epoch = steps_per_epoch,
    validation_data = test_dataset,
    validation_steps = validation_steps,
    epochs = num_epochs,
    callbacks = [tensorboard, cm_callback]
)

Epoch 1/10
31/31 [==============================] - ETA: 0s - loss: 1.5649 - accuracy: 0.4446

C:\Users\hapet\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:25: RuntimeWarning: invalid value encountered in true_divide


31/31 [==============================] - 17s 542ms/step - loss: 1.5649 - accuracy: 0.4446 - val_loss: 1.9283 - val_accuracy: 0.3438
Epoch 2/10
31/31 [==============================] - 19s 627ms/step - loss: 1.4839 - accuracy: 0.4855 - val_loss: 1.9623 - val_accuracy: 0.3286
Epoch 3/10
31/31 [==============================] - 19s 623ms/step - loss: 1.4620 - accuracy: 0.4783 - val_loss: 1.9382 - val_accuracy: 0.3478
Epoch 4/10
31/31 [==============================] - 19s 624ms/step - loss: 1.4459 - accuracy: 0.5207 - val_loss: 1.8530 - val_accuracy: 0.3458
Epoch 5/10
31/31 [==============================] - 18s 573ms/step - loss: 1.4641 - accuracy: 0.4814 - val_loss: 1.8315 - val_accuracy: 0.3528
Epoch 6/10
31/31 [==============================] - 18s 586ms/step - loss: 1.3345 - accuracy: 0.5320 - val_loss: 1.8591 - val_accuracy: 0.3629
Epoch 7/10
31/31 [==============================] - 16s 518ms/step - loss: 1.3215 - accuracy: 0.5424 - val_loss: 1.8249 - val_accuracy: 0.3821
Epoch 8/10

### expert

In [56]:
loss_object = tf.keras.losses.SparseCategoricalCrossentropy()

optimizer = tf.keras.optimizers.Adam()

In [59]:
train_loss = tf.keras.metrics.Mean(name = 'train_loss')
train_accuracy = tf.keras.metrics.SparseCategoricalAccuracy(name = 'train_accuracy')

test_loss = tf.keras.metrics.Mean(name = 'train_loss')
test_accuracy = tf.keras.metrics.SparseCategoricalAccuracy(name = 'train_accuracy')


In [75]:
@tf.function
def train_step(images, labels):
    with tf.GradientTape() as tape:
        predictions = model(images)
        loss = loss_object(labels, predictions)
    gradients = tape.gradient(loss, model.trainable_variables)
    
    train_loss(loss)
    train_accuracy(labels, predictions)

In [76]:
@tf.function
def test_step(images, labels):
    predictions = model(images)
    t_loss = loss_object(labels, predictions)
    
    test_loss(t_loss)
    test_accuracy(labels, predictions)

In [77]:
logdir = os.path.join('jogs', datetime.now().strftime('%Y%m%d-%H%M%S'))

In [78]:
file_write = tf.summary.create_file_writer(logdir)

In [83]:
for epoch in range(num_epochs):
    print('start epoch', num_epochs)
    for step, (images, labels) in enumerate(train_dataset):
        print(step, images,labels )
        train_step(images, labels)
    print('start_ callback')
    with file_write.as_default():
        tf.summary.image('input_image', images, step = step+(step*epoch))
        tf.summary.scalar('train_loss', train_loss.result(), step = step+(step*epoch))
        tf.synnary.scalar('train_accuracy', train_accuracy.result(), step = step+(step*epoch))
    print('start test')
    for test_images, test_labels in test_dataset:
        test_step(test_images, test_labels)
        
    template = "Epoch {}, loss: {}, accuracy : {}, test_loss : {}, test_accuracy : {}"
    print(template.format(epoch + 1,
                         train_loss.result(),
                         train_accuracy.result()*100,
                         test_loss.result(),
                         test_accuracy.result()*100))

start epoch 10
0 tf.Tensor(
[[[[0.5803922  0.4862745  0.40392157]
   [0.59607846 0.49019608 0.4       ]
   [0.61960787 0.5176471  0.42352942]
   ...
   [0.19607843 0.1882353  0.16862746]
   [0.16862746 0.18039216 0.1764706 ]
   [0.23137255 0.24313726 0.24705882]]

  [[0.47843137 0.34117648 0.22352941]
   [0.46666667 0.3254902  0.19607843]
   [0.48235294 0.34509805 0.21568628]
   ...
   [0.07058824 0.03137255 0.        ]
   [0.         0.         0.        ]
   [0.0627451  0.07843138 0.07843138]]

  [[0.42745098 0.28627452 0.16470589]
   [0.47058824 0.32941177 0.19607843]
   [0.4627451  0.32941177 0.19607843]
   ...
   [0.19215687 0.10588235 0.03137255]
   [0.0627451  0.02745098 0.        ]
   [0.09803922 0.09411765 0.08235294]]

  ...

  [[0.20784314 0.13333334 0.07843138]
   [0.21960784 0.12156863 0.02745098]
   [0.627451   0.52156866 0.27450982]
   ...
   [0.7764706  0.6313726  0.10196079]
   [0.7882353  0.6        0.13333334]
   [0.8156863  0.6666667  0.3764706 ]]

  [[0.3254902  0.

2 tf.Tensor(
[[[[0.4117647  0.44705883 0.34509805]
   [0.43137255 0.3882353  0.3254902 ]
   [0.34901962 0.29411766 0.24313726]
   ...
   [0.4627451  0.42352942 0.38431373]
   [0.4        0.33333334 0.28627452]
   [0.45490196 0.3529412  0.29411766]]

  [[0.5019608  0.5137255  0.43529412]
   [0.47843137 0.42352942 0.37254903]
   [0.34901962 0.2784314  0.23921569]
   ...
   [0.40392157 0.36078432 0.30980393]
   [0.5019608  0.3882353  0.34509805]
   [0.45490196 0.30588236 0.24705882]]

  [[0.5764706  0.57254905 0.5019608 ]
   [0.47058824 0.41960785 0.3647059 ]
   [0.3764706  0.3019608  0.25490198]
   ...
   [0.49019608 0.41960785 0.3647059 ]
   [0.50980395 0.3529412  0.30980393]
   [0.63529414 0.43529412 0.38039216]]

  ...

  [[0.2784314  0.30588236 0.2       ]
   [0.36078432 0.40784314 0.28235295]
   [0.37254903 0.44313726 0.29803923]
   ...
   [0.24705882 0.23529412 0.20392157]
   [0.32941177 0.3019608  0.24313726]
   [0.36862746 0.3372549  0.27058825]]

  [[0.24705882 0.28627452 0.1921

6 tf.Tensor(
[[[[0.1882353  0.16862746 0.08627451]
   [0.21960784 0.2        0.09803922]
   [0.25490198 0.23529412 0.11764706]
   ...
   [0.29411766 0.27450982 0.14117648]
   [0.30588236 0.2901961  0.15294118]
   [0.3019608  0.28627452 0.14901961]]

  [[0.21176471 0.19215687 0.10588235]
   [0.23137255 0.21568628 0.11372549]
   [0.24705882 0.22745098 0.11764706]
   ...
   [0.29411766 0.27450982 0.14901961]
   [0.2784314  0.25882354 0.13333334]
   [0.29411766 0.2784314  0.14901961]]

  [[0.22352941 0.20392157 0.11764706]
   [0.21960784 0.2        0.10196079]
   [0.24313726 0.21960784 0.11764706]
   ...
   [0.2627451  0.24313726 0.1254902 ]
   [0.2509804  0.22745098 0.11764706]
   [0.27450982 0.25490198 0.14117648]]

  ...

  [[0.30588236 0.27450982 0.26666668]
   [0.29803923 0.26666668 0.25882354]
   [0.28627452 0.25490198 0.24313726]
   ...
   [0.5254902  0.47058824 0.31764707]
   [0.49019608 0.4392157  0.29803923]
   [0.50980395 0.47058824 0.34117648]]

  [[0.31764707 0.28627452 0.2784

10 tf.Tensor(
[[[[0.3882353  0.5372549  0.22745098]
   [0.40784314 0.5764706  0.23921569]
   [0.4        0.59607846 0.23529412]
   ...
   [0.47058824 0.65882355 0.25490198]
   [0.40392157 0.5764706  0.20392157]
   [0.28627452 0.4509804  0.14117648]]

  [[0.4        0.5529412  0.24313726]
   [0.40392157 0.5686275  0.23529412]
   [0.39215687 0.5803922  0.22352941]
   ...
   [0.42745098 0.6117647  0.22352941]
   [0.40784314 0.58431375 0.21176471]
   [0.38431373 0.56078434 0.20392157]]

  [[0.4392157  0.6        0.27450982]
   [0.4117647  0.5803922  0.24705882]
   [0.40784314 0.58431375 0.23529412]
   ...
   [0.40784314 0.5882353  0.21176471]
   [0.40784314 0.58431375 0.21176471]
   [0.41960785 0.6        0.21176471]]

  ...

  [[0.53333336 0.6901961  0.34509805]
   [0.5137255  0.68235296 0.32941177]
   [0.52156866 0.69803923 0.3372549 ]
   ...
   [0.5254902  0.6901961  0.32941177]
   [0.5137255  0.6862745  0.32156864]
   [0.5254902  0.70980394 0.3372549 ]]

  [[0.5254902  0.6784314  0.325

14 tf.Tensor(
[[[[0.2        0.21568628 0.14509805]
   [0.2784314  0.3019608  0.19607843]
   [0.31764707 0.34901962 0.18039216]
   ...
   [0.6156863  0.70980394 0.8235294 ]
   [0.60784316 0.7019608  0.81960785]
   [0.6039216  0.7019608  0.8156863 ]]

  [[0.23137255 0.25882354 0.13333334]
   [0.33333334 0.3647059  0.2       ]
   [0.36862746 0.4117647  0.18431373]
   ...
   [0.65882355 0.7372549  0.8235294 ]
   [0.6627451  0.7411765  0.827451  ]
   [0.6666667  0.7411765  0.83137256]]

  [[0.32156864 0.35686275 0.17254902]
   [0.34901962 0.39215687 0.16862746]
   [0.38431373 0.43529412 0.16470589]
   ...
   [0.7411765  0.79607844 0.84705883]
   [0.78039217 0.8352941  0.8862745 ]
   [0.7921569  0.84705883 0.8980392 ]]

  ...

  [[0.57254905 0.5647059  0.5568628 ]
   [0.5019608  0.50980395 0.49803922]
   [0.36078432 0.36862746 0.36078432]
   ...
   [0.5647059  0.5686275  0.57254905]
   [0.56078434 0.5647059  0.56078434]
   [0.5647059  0.56078434 0.5647059 ]]

  [[0.56078434 0.56078434 0.552

...

346 tf.Tensor(
[[[[0.8117647  0.8156863  0.8156863 ]
   [0.8117647  0.8156863  0.8117647 ]
   [0.8117647  0.8117647  0.8039216 ]
   ...
   [0.84705883 0.85490197 0.8784314 ]
   [0.8392157  0.84313726 0.8627451 ]
   [0.8352941  0.8392157  0.85882354]]

  [[0.8235294  0.827451   0.83137256]
   [0.8235294  0.83137256 0.8235294 ]
   [0.8235294  0.8235294  0.8156863 ]
   ...
   [0.85490197 0.87058824 0.89411765]
   [0.8509804  0.85490197 0.8784314 ]
   [0.84705883 0.8509804  0.87058824]]

  [[0.8156863  0.8235294  0.8235294 ]
   [0.81960785 0.8235294  0.81960785]
   [0.81960785 0.81960785 0.8117647 ]
   ...
   [0.8509804  0.8666667  0.8862745 ]
   [0.84705883 0.85490197 0.87058824]
   [0.84313726 0.84705883 0.8666667 ]]

  ...

  [[0.34901962 0.32941177 0.2784314 ]
   [0.47058824 0.45882353 0.4117647 ]
   [0.70980394 0.7137255  0.7058824 ]
   ...
   [0.2901961  0.2627451  0.21568628]
   [0.2509804  0.22745098 0.1764706 ]
   [0.19215687 0.1764706  0.13725491]]

  [[0.40784314 0.39215687 0.35

350 tf.Tensor(
[[[[0.5019608  0.56078434 0.45882353]
   [0.4392157  0.5019608  0.37254903]
   [0.4392157  0.50980395 0.34901962]
   ...
   [0.34117648 0.45490196 0.36078432]
   [0.2627451  0.38039216 0.26666668]
   [0.20392157 0.3254902  0.18039216]]

  [[0.42745098 0.47843137 0.38431373]
   [0.36862746 0.41960785 0.30588236]
   [0.4        0.45490196 0.32156864]
   ...
   [0.25882354 0.36862746 0.23529412]
   [0.23137255 0.3372549  0.20784314]
   [0.2        0.30980393 0.16862746]]

  [[0.5137255  0.5294118  0.54901963]
   [0.46666667 0.4862745  0.49411765]
   [0.4509804  0.4745098  0.4745098 ]
   ...
   [0.2509804  0.34117648 0.26666668]
   [0.25882354 0.34901962 0.2784314 ]
   [0.21960784 0.30980393 0.23137255]]

  ...

  [[0.42745098 0.54901963 0.24705882]
   [0.40784314 0.5254902  0.22352941]
   [0.43137255 0.5568628  0.24313726]
   ...
   [0.4392157  0.5647059  0.2627451 ]
   [0.44705883 0.57254905 0.27450982]
   [0.45882353 0.5882353  0.28627452]]

  [[0.4        0.52156866 0.20

354 tf.Tensor(
[[[[0.3019608  0.2901961  0.21176471]
   [0.31764707 0.28627452 0.23921569]
   [0.3019608  0.28627452 0.27058825]
   ...
   [0.27450982 0.30588236 0.21960784]
   [0.3137255  0.35686275 0.27450982]
   [0.21176471 0.2627451  0.1882353 ]]

  [[0.3254902  0.29803923 0.22352941]
   [0.38039216 0.34901962 0.29803923]
   [0.28235295 0.27058825 0.24705882]
   ...
   [0.31764707 0.36862746 0.2509804 ]
   [0.29411766 0.34117648 0.23529412]
   [0.24705882 0.28627452 0.19215687]]

  [[0.36862746 0.3372549  0.27058825]
   [0.32941177 0.3019608  0.24313726]
   [0.24705882 0.23529412 0.20392157]
   ...
   [0.37254903 0.44313726 0.29803923]
   [0.36078432 0.40784314 0.28235295]
   [0.2784314  0.30588236 0.2       ]]

  ...

  [[0.63529414 0.43529412 0.38039216]
   [0.50980395 0.3529412  0.30980393]
   [0.49019608 0.41960785 0.3647059 ]
   ...
   [0.3764706  0.3019608  0.25490198]
   [0.47058824 0.41960785 0.3647059 ]
   [0.5764706  0.57254905 0.5019608 ]]

  [[0.45490196 0.30588236 0.24

   [0.05490196 0.0627451  0.03529412]]]], shape=(32, 32, 32, 3), dtype=float32) tf.Tensor([9 1 0 8 0 9 8 4 0 2 1 4 2 7 1 7 0 5 2 9 7 9 8 6 4 4 1 1 6 7 8 8], shape=(32,), dtype=int64)
358 tf.Tensor(
[[[[0.1882353  0.16862746 0.08627451]
   [0.21960784 0.2        0.09803922]
   [0.25490198 0.23529412 0.11764706]
   ...
   [0.29411766 0.27450982 0.14117648]
   [0.30588236 0.2901961  0.15294118]
   [0.3019608  0.28627452 0.14901961]]

  [[0.21176471 0.19215687 0.10588235]
   [0.23137255 0.21568628 0.11372549]
   [0.24705882 0.22745098 0.11764706]
   ...
   [0.29411766 0.27450982 0.14901961]
   [0.2784314  0.25882354 0.13333334]
   [0.29411766 0.2784314  0.14901961]]

  [[0.22352941 0.20392157 0.11764706]
   [0.21960784 0.2        0.10196079]
   [0.24313726 0.21960784 0.11764706]
   ...
   [0.2627451  0.24313726 0.1254902 ]
   [0.2509804  0.22745098 0.11764706]
   [0.27450982 0.25490198 0.14117648]]

  ...

  [[0.30588236 0.27450982 0.26666668]
   [0.29803923 0.26666668 0.25882354]
   [0.28

KeyboardInterrupt: 